# Final Exam
# Machine Learning 2015-2

After solving all the questions in the exam save your notebook with the name `username.ipynb` and submit it to: https://www.dropbox.com/request/KN8GwdAIi0Hl2jk2mg2E

---

The following code implements a simple one-neuron neural network:

In [1]:
import numpy as np
import pylab as pl
%matplotlib inline

def sigmoid(x):
    return 1.0/(1.0 + np.exp(-x))

def predict(w, x):
    x = np.append(np.array([1]), x)
   
    return sigmoid(np.dot(w, x))



### 1. (1.0)
Find a weight vector such that the neural network calculates the NOR function:
    
$$f(x,y)=\neg(x\vee y)$$

Use the following function to test your answer:

In [2]:
def test_prediction(X, Y, w):
    epsilon = 0.001
    for i, x in enumerate(X):
        if np.abs(predict(w, x) - Y[i]) > epsilon:
            
            raise Exception("Prediction error")
    return True

X = [[0, 0],
 [0, 1],
 [1, 0],
 [1, 1]]
Y = [1, 0, 0 ,0]
w = np.array([10, -20, -20])
test_prediction(X, Y, w)

True

### 2. (1.0)

The following function calculates the loss function of the neural network

In [3]:
def loss(w, x, y):
    return (predict(w, x) - y) ** 2 / 2

Write a function that calculates the gradient of the loss with respect to the weights:

$$ \frac{\partial E}{\partial w} $$

In [4]:
def dsig(x):
    
    return x*(1-x)
def de_dw(w, x, y):
    delta = np.zeros(len(w))
      
    val=(predict(w,x)-y)*dsig(predict(w,x))
    x = np.append(np.array([1]), x)
    delta=val*x
    # put your code here
    return delta

Use the following functions to test your code:

In [5]:
def num_de_dw(w, x, y, epsilon):
    deltas = np.identity(len(w)) * epsilon
    de = np.zeros(len(w))
    for i in range(len(w)):
        de[i] = (loss(w + deltas[i, :], x, y) - loss(w - deltas[i, :], x, y)) / (2 * epsilon)
    return de

def test_de_dw():
    num_tests = 100
    epsilon = 0.0001
    for i in range(num_tests):
        tw = np.random.randn(3)
        tx = np.random.randn(2)
        ty = np.random.randn(1)
        print (de_dw(tw, tx,ty)) 
        print (num_de_dw(tw, tx, ty, epsilon))
        if np.linalg.norm(de_dw(tw, tx,ty) - num_de_dw(tw, tx, ty, epsilon)) > epsilon:
            raise Exception("de_dw test failed!")

test_de_dw()

[ 0.00361838  0.00278242 -0.0038118 ]
[ 0.00361838  0.00278242 -0.0038118 ]
[-0.04035732 -0.05140127  0.04998526]
[-0.04035732 -0.05140127  0.04998526]
[ 0.02188831  0.01112613  0.02292367]
[ 0.02188831  0.01112613  0.02292367]
[ 0.03404092 -0.00240233 -0.05807317]
[ 0.03404092 -0.00240233 -0.05807317]
[ 0.52423482  0.14721585  0.14591704]
[ 0.52423482  0.14721585  0.14591704]
[ 0.22546929 -0.08998641  0.11208553]
[ 0.22546929 -0.08998641  0.11208553]
[ 0.04533799  0.00898872 -0.011983  ]
[ 0.04533799  0.00898872 -0.011983  ]
[ 0.09861583 -0.09234696 -0.21875542]
[ 0.09861583 -0.09234696 -0.21875542]
[ 0.05877143 -0.02940076  0.03116671]
[ 0.05877143 -0.02940076  0.03116671]
[ 0.11931123 -0.02702918 -0.06524697]
[ 0.11931123 -0.02702918 -0.06524697]
[ 0.43251664 -0.56064835 -0.80653295]
[ 0.43251664 -0.56064835 -0.80653295]
[ 0.32120464  0.09854823 -0.21391254]
[ 0.32120464  0.09854823 -0.21391254]
[ 0.20352592 -0.01110682  0.05591738]
[ 0.20352592 -0.01110682  0.05591738]
[ 0.01208132

Now, we can use the gradient function to train the neural network using gradient descent

In [6]:
def evaluate(w, X, Y):
    result = 0
    for i, x in enumerate(X):
        result += loss(w, x, Y[i])
    return result

def train(X, Y, epochs, eta, w_ini):
    losses = []
    w = w_ini
    for i in range(epochs):
        delta = np.zeros(len(w))
        for i, x in enumerate(X):
            delta += de_dw(w, x, Y[i])
        w = w - eta * delta
        losses.append(evaluate(w, X, Y))
    return w, losses

In [7]:
X = [[0, 0],
     [0, 1],
     [1, 0],
     [1, 1]]
Y = [0, 0, 1, 0]
w, losses = train(X, Y, 50, 10, [0, 0, 0])
pl.plot(losses)
print w
print predict(w, [1, 0])
print predict(w, [0, 1])

[-2.75411492  5.35754647 -5.59430763]
0.93108210251
0.000236713671518


### 3. (1.0)

Now we will modify the loss function to include a regularization term:
$$ E(w,D)=\frac{1}{2}\sum_{(x_{i},y_{i})\in D}(f(w,x_{i})-y_{i})^{2}+\frac{\text{1}}{2}\beta\left\Vert w\right\Vert _{2}^{2}$$

where $f(w,x_{i})$ is the prediction calculated by the neural network.

To accomplish this you must modify the following functions:

In [8]:
def reg_loss(w, beta, x, y):
    loss = (((predict(w, x) - y) ** 2)/2)+(1/4*beta*np.dot(w,w))
    return loss

def reg_de_dw(w, beta, x, y):
    delta = np.zeros(len(w))
    delta= de_dw(w,x,y)+(1/2*beta*w)
    # put your code here
    return delta

You can use the following functions to test your code:

In [9]:
def reg_num_de_dw(w, beta, x, y, epsilon):
    deltas = np.identity(len(w)) * epsilon
    de = np.zeros(len(w))
    for i in range(len(w)):
        de[i] = (reg_loss(w + deltas[i, :], beta, x, y) - reg_loss(w - deltas[i, :], beta, x, y)) / (2 * epsilon)
    return de

def reg_test_de_dw():
    num_tests = 100
    epsilon = 0.0001
    beta = 1
    for i in range(num_tests):
        tw = np.random.randn(3)
        tx = np.random.randn(2)
        ty = np.random.randn(1)
                 
        if np.linalg.norm(reg_de_dw(tw, beta, tx, ty) - reg_num_de_dw(tw, beta, tx, ty, epsilon)) > epsilon:
            raise Exception("reg_de_dw test failed!")

reg_test_de_dw()

### 4. (1.0)
Now train the neural network using regularization:

In [10]:
def reg_evaluate(w, beta, X, Y):
    result = 0
    for i, x in enumerate(X):
        result += reg_loss(w,beta, x, Y[i])
    return result

def reg_train(X, Y, epochs, eta, w_ini, beta):
    losses = []
    w = np.array(w_ini)
    for i in range(epochs):
        delta = np.zeros(len(w))
        for i, x in enumerate(X):
            delta += reg_de_dw(w,beta, x, Y[i])
        w = w - eta * delta
        losses.append(reg_evaluate(w,beta, X, Y))
    
    # your code here
    return w, losses

In [11]:
X = [[0, 0],
     [0, 1],
     [1, 0],
     [1, 1]]
Y = [0, 0, 1, 0]
wr, losses = reg_train(X, Y, 50, 2, [0, 0, 0], 0.01)
pl.plot(losses)
print wr
print predict(wr, [1, 0])
print predict(wr, [0, 1])

[-1.73530979  3.28436986 -3.55201031]
0.824777934667
0.00502986236723


What is the effect of regularization? Discuss.

### 5. (1.0)
Here, we will build a kernel version of the previous neural network, i.e., a neural network able to work in a 
feature space induced by a kernel. To do this we will express the weight vector as a linear combination of vectors in a set $X$:

$$ w=\sum_{x_{i}\in X}\alpha_{i}\phi(x_{i}) $$

Now, implement this modifying the following functions:

In [12]:
def k_predict(alpha, X, kernel, x):
    
    result = 0
    weight= np.dot(alpha,kernel(X,x))
    x = np.append(np.array([1]), x)
    result= np.dot(weight,x)
    # your code here
    return sigmoid(result)
    
def k_loss(alpha, X, beta, kernel, x, y):
    w=np.dot(alpha,kernel(X,x))
    loss = (((k_predict(alpha,X,kernel, x) - y) ** 2)/2)+(1/4*beta*np.dot(w,w))
    # your code here
    return loss

Test your functions with the following code:

In [13]:
alpha = [1, 0.5, -0.3, -0.4]
Xs = [[0.1, -0.5],
     [0.5, 1.0],
     [-1.0, 0.5],
     [1.0, 1.0]]

def k1(x, y):
    return np.dot(x, y)

def k2(x, y):
    return (np.dot(x, y) + 1) ** 2

X = [[0, 0],
     [0, 1],
     [1, 0],
     [1, 1]]
Y = [0, 0, 1, 0]
for i, x in enumerate(X):
    print k_predict(alpha, Xs, k1, x), k_loss(alpha, Xs, 1, k1, x, Y[i])
print "--------"
for i, x in enumerate(X):
    print k_predict(alpha, Xs, k2, x), k_loss(alpha, Xs, 1, k2, x, Y[i])

[ 0.5  0.5  0.5] [ 0.125  0.125  0.125]
[ 0.36586441  0.5         0.36586441] [ 0.06692838  0.125       0.06692838]
[ 0.5621765  0.5621765  0.5      ] [ 0.09584471  0.09584471  0.125     ]
[ 0.42555748  0.42555748  0.42555748] [ 0.09054959  0.09054959  0.09054959]
--------
[ 0.68997448  0.5         0.5       ] [ 0.23803239  0.125       0.125     ]
[ 0.49375033  0.5         0.49375033] [ 0.12189469  0.125       0.12189469]
[ 0.67590153  0.67590153  0.5       ] [ 0.05251991  0.05251991  0.125     ]
[ 0.45264238  0.45264238  0.45264238] [ 0.10244256  0.10244256  0.10244256]


### 6. (optional, extra credit)

Train the kernel neural network using gradient descent.

In [14]:
def k_de_dw(alpha, X, beta, kernel, x, y):
    w=np.dot(alpha,kernel(X,x))
    delta = 0
    
    val=(k_predict(alpha,X,kernel, x) - y)*dsig(k_predict(alpha,X,kernel, x))
    
    x = np.append(np.array([1]), x)
    delta=val*x
    delta=delta+(1/2*beta*w)
    
    # put your code here
    return delta

In [15]:
def k_evaluate(alpha, X, beta, kernel, X_, Y):
    result = 0
    for i, x in enumerate(X_):
        result += k_loss(alpha, X, beta, kernel, x, Y[i])
    return result

def k_train(X, Y, epochs, eta, w_ini, beta,alpha,X_,kernel):
    losses = []
    w = np.array(w_ini)
    for i in range(epochs):
        delta = 0
        for i, x in enumerate(X_):
            delta += k_de_dw(alpha, X, beta, kernel, x, Y[i])
        w = w - eta * delta
        losses.append(k_evaluate(alpha, X, beta, kernel, x, Y))
    
    # your code here
    return w, losses

In [16]:
alpha = [1, 0.5, -0.3, -0.4]
Xs = [[0.1, -0.5],
     [0.5, 1.0],
     [-1.0, 0.5],
     [1.0, 1.0]]

def k1(x, y):
    return np.dot(x, y)

def k2(x, y):
    return (np.dot(x, y) + 1) ** 2

X = [[0, 0],
     [0, 1],
     [1, 0],
     [1, 1]]
Y = [0, 0, 1, 0]
wr, losses = k_train(Xs, Y, 50, 2, [0, 0, 0], 0.01,alpha,X,k2)
pl.plot(losses)
print wr
print predict(wr, [1, 0])
print predict(wr, [0, 1])

[-31.2159388   -4.11488599 -23.55637307]
4.52916096464e-16
1.63187614121e-24
